# Retrieving data from Kiva API

We will be using [KIVA](https://www.kiva.org/) data for the entirety of this course. Kiva makes it's data publically available through it's [API](http://build.kiva.org/). 

Not sure what an API is? It stands for Application Program Interface. **To a data scientist, it's an incredible way for you to access and selectively pull data.** Whereas many APIs are not open for public access, Kiva's is, giving us wide access to rich datasets.  

For more on APIs, CodeAcademy has a fantastic short course (link [here](https://www.codecademy.com/en/tracks/placekitten) that introduces you to APIs and allows you to pull images of kittens from a website by the end of the session.

----

Let's setup what we need:

In [1]:
reset -fs

In [2]:
import os
import json
import logging
import time
from urllib.request import urlopen, Request

from pandas.io.json import json_normalize
import pandas as pd
import requests

pd.set_option('display.max_columns', 80)

The cell below enables Jupyter to show the output of multiple cells at once. There are a lot of cool jupyter specific commands to allow you to work faster. [Here](https://www.dataquest.io/blog/jupyter-notebook-tips-tricks-shortcuts/) is a great article that goes through some less well known shortcuts and tricks.

In [3]:
from IPython.core.interactiveshell import InteractiveShell

InteractiveShell.ast_node_interactivity = "all"

In the cell below we set the maximum number of columns to 100 so we can see our entire data set. If we did not set this option, we would not be able to see some columns in our dataset.

In [4]:
pd.set_option('display.max_columns', 100) 

----
Exploring Kiva API
-----

There is great documentation on Kiva's API [here](http://build.kiva.org/api). The documentation explains what parameters (conditions) we need to pass in our request to Kiva's database in order to get the data we want.

We are trying to retrive all Kiva data from Kenya. So we will be using two main parameters where we set country_code=KE (KE is the two letter [ISO](https://en.wikipedia.org/wiki/ISO_3166-2) code for Kenya), and we increase the results per page to 500 (this is the maximum KIVAs API appears to allow). You can see the HTML results of the api call by pasting the url below into your browser, HTML is a format that is really easy to read.

http://api.kivaws.org/v1/loans/search/?country_code=KE&per_page=500

1) Go ahead and play with the url in order to retrieve different data. For example, how would you retrieve data from South Africa (ZA)?

2) How would you only retrive 200 results?

Answers:

1) http://api.kivaws.org/v1/loans/search/?country_code=ZA&per_page=500

2)  http://api.kivaws.org/v1/loans/search/?country_code=ZA&per_page=200



We want to request this data from the api and store it in a format that is more intuitive to us - a dataframe. Let's get started. The code below retrieves the first 500 results and converts it into a pandas dataframe. You will get to know a lot more about dataframes over the next few classes.

In [59]:
r = requests.get('http://api.kivaws.org/v1/loans/search.json?country_code=KE&per_page=500')

In [5]:
r = requests.get('http://api.kivaws.org/v1/loans/search.json?country_code=KE&per_page=500')

Notice that in the request above we specify json as the type of text we want returned. This is easier to handle and change into a python dataframe. You can past the link into your browser to understand the difference between [JSON](https://en.wikipedia.org/wiki/JSON) and [HTML](https://en.wikipedia.org/wiki/HTML).

By running r.headers below we can see all the data associated with our request.

It shows the time of our request, the fact that we are requesting json text 'Content-Type': 'application/json; charset=UTF-8', in addition to other details.

In [80]:
print(*r.headers.items(), sep='\n')

('Date', 'Wed, 20 Sep 2017 15:52:00 GMT')
('Server', 'Apache/2.4.7 (Ubuntu)')
('Access-Control-Allow-Origin', '*')
('Expires', 'Tue, 03 Jul 2001 06:00:00 GMT')
('Last-Modified', 'Wed, 20 Sep 2017 15:52:00 GMT')
('Cache-Control', 'private, no-store, no-cache, must-revalidate, max-age=0, post-check=0, pre-check=0, proxy-revalidate, no-transform')
('Pragma', 'no-cache')
('X-RateLimit-Overall-Limit', '60')
('X-RateLimit-Overall-Remaining', '60')
('Vary', 'Accept-Encoding')
('Content-Encoding', 'gzip')
('Content-Length', '26498')
('Content-Type', 'application/json; charset=UTF-8')


By running the command r.json() below we can get an idea of what our data looks like before we change it into a pandas data frame. 

In [61]:
r.json()

{'loans': [{'activity': 'Farming',
   'basket_amount': 0,
   'bonus_credit_eligibility': False,
   'borrower_count': 5,
   'description': {'languages': ['en']},
   'funded_amount': 0,
   'id': 1377060,
   'image': {'id': 2634943, 'template_id': 1},
   'lender_count': 0,
   'loan_amount': 500,
   'location': {'country': 'Kenya',
    'country_code': 'KE',
    'geo': {'level': 'town', 'pairs': '0.05 35.716667', 'type': 'point'},
    'town': 'ELDAMA RAVINE'},
   'name': 'Luita Women Group',
   'partner_id': 388,
   'planned_expiration_date': '2017-10-20T15:50:04Z',
   'posted_date': '2017-09-20T15:50:04Z',
   'sector': 'Agriculture',
   'status': 'fundraising',
   'tags': [],
   'use': 'to buy seeds and fertilizer for her farmland.'},
  {'activity': 'Home Energy',
   'basket_amount': 0,
   'bonus_credit_eligibility': False,
   'borrower_count': 1,
   'description': {'languages': ['en']},
   'funded_amount': 0,
   'id': 1376958,
   'image': {'id': 2634862, 'template_id': 1},
   'lender_coun

`json.loads` turns the json object into a python object.

In [62]:
data = json.loads(r.text)

`json_normalize` normalizes semi-structured json data into a flat table

In [63]:
loans = json_normalize(data['loans'])

We have now extracted the first 500 rows of loans from the API. We can confirm how many rows we have in a dataset using the len() function below. Now, we need to extract this data more systematically for all Kenyan loan results. KIVA has a parameter called page but does not allow for range of pages, so we will have to create a python loop to go through each page of results and add to our dataset.

In [64]:
len(loans.index)

500

In the function defined below we are doing a few things. Firstly, we create an empty dataframe, then we loop through each page and call the api. We add the results of each page to our dataframe.

The first part of the code extracts all the loans in Kenya, the second part of the function extracts additional loan information (like the longer description about the loan) by making a second api call. This is inserted in a second dataframe called loans_details. There is a restriction on the second API call which only allows us to pass 100 loans in one call. To address this, we have a parameter in `pages=100` which means we only extract 100 loans in every call which allows us to satisfy the second restriction.

In [23]:
def extract_loans(n_pages, country_iso_code):

    loans_full = pd.DataFrame()
    loans_details = pd.DataFrame()
    
    for n in range(1, n_pages+1):
        print("Requesting page: {}".format(n))
        r = requests.get('http://api.kivaws.org/v1/loans/search.json?country_code='+country_iso_code+'&per_page=100&page='+str(n))
        data = json.loads(r.text)
        loans = json_normalize(data['loans'])
        
        if data['paging']['total'] == 0:
            break # Stop if there are no loans
            
        # Take the loan id column from our retrieved loan data, and use it to pull additional details
        # about our loans. We store this in a seperate table loans_details
        
        loan_ids = loans['id'].tolist()
        loan_ids_str = ','.join(str(e) for e in loan_ids)
        r = requests.get('https://api.kivaws.org/v1/loans/'+loan_ids_str+'.json')
        ld_data = json.loads(r.text)
        loans_ext = json_normalize(ld_data['loans'])
        loans_details = loans_details.append(loans_ext, ignore_index=True)
         
        loans_full = loans_full.append(loans,ignore_index=True)
        print("The number of loans on current page: {}".format(len(loans_full.index)))
        time.sleep(.5) # Wait a little while to so we don't overload Kiva servers
        
    return loans_full, loans_details

In [24]:
country_codes = ["DZ", "AO", "SH", "BJ", "BW", "BF", "BI", "CM", "CV", "CF", "TD", "KM", "CG", "CD", "DJ", "EG", "GQ", "ER", "SZ", "ET", "GA", "GM", "GH", "GN", "GW", "CI", "KE", "LS", "LR", "LY", "MG", "MW", "ML", "MR", "MU", "YT", "MA", "MZ", "NA", "NE", "NG", "ST", "RE", "RW", "ST", "SN", "SC", "SL", "SO", "ZA", "SS", "SH", "SD", "SZ", "TZ", "TG", "TN", "UG", "CD", "ZM", "TZ", "ZW"]

In [19]:
# country_iso_code = 'DZ'
# n=1
# r = requests.get('http://api.kivaws.org/v1/loans/search.json?country_code='+country_iso_code+'&per_page=100&page='+str(n))
# data = json.loads(r.text)
# loans = json_normalize(data['loans'])

In [25]:
loans_full_complete = pd.DataFrame()
loans_details_complete = pd.DataFrame()

for code in country_codes:
    loans_full, loans_details = extract_loans(n_pages=1, country_iso_code=code)  
    loans_full_complete.append(loans_full)
    loans_details_complete.append(loans_details)

Requesting page: 1


Empty DataFrame
Columns: []
Index: []

Empty DataFrame
Columns: []
Index: []

Requesting page: 1


Empty DataFrame
Columns: []
Index: []

...

Requesting page: 1


Empty DataFrame
Columns: []
Index: []

Empty DataFrame
Columns: []
Index: []

Requesting page: 1


KeyboardInterrupt: 

In [ ]:
loans_full_complete.shape

# TODO: Refactor below this cell 

-----

Let's save our data!

In [79]:
path = '../../../data/'
loans_full.to_csv(path+'loans_full_large.csv')
loans_details.to_csv(path+'loans_details.csv')

We will also pull data about Kiva's partners, who are the intermediaries between Kiva and end recipients for the majority of loans made.

In [2]:
data_path = '~/intro_to_machine_learning/data'
df=pd.read_csv(data_path+'/loans_details.csv', low_memory=False)
df.head()

In [54]:
df=df[df['partner_id'].notnull()]
df['partner_id']=df['partner_id'].astype(int).astype(str)
partner_id=df['partner_id'].unique().tolist()

In [28]:
d = r.get('https://api.kivaws.org/v1/partners/322.json?app_id=org.deltanalytics')

In [29]:
d.headers

{'Date': 'Tue, 30 May 2017 07:02:52 GMT', 'Server': 'Apache/2.4.7 (Ubuntu)', 'Access-Control-Allow-Origin': '*', 'Expires': 'Tue, 03 Jul 2001 06:00:00 GMT', 'Last-Modified': 'Tue, 30 May 2017 07:02:52 GMT', 'Cache-Control': 'private, no-store, no-cache, must-revalidate, max-age=0, post-check=0, pre-check=0, proxy-revalidate, no-transform', 'Pragma': 'no-cache', 'X-RateLimit-Overall-Limit': '500', 'X-RateLimit-Overall-Remaining': '500', 'Vary': 'Accept-Encoding', 'Content-Encoding': 'gzip', 'Content-Length': '1255', 'Content-Type': 'application/json; charset=UTF-8'}

In [30]:
d.json();

{'lenders': [{'country_code': 'AU',
   'image': {'id': 2543858, 'template_id': 1},
   'lender_id': 'melbournesolar4571',
   'name': 'Melbourne Solar Solutions',
   'uid': 'melbournesolar4571',
   'whereabouts': 'Dandenong VIC'},
  {'image': {'id': 2543855, 'template_id': 1},
   'lender_id': 'shahab7717',
   'name': 'Shahab',
   'uid': 'shahab7717',
   'whereabouts': ''},
  {'country_code': 'GB',
   'image': {'id': 2543849, 'template_id': 1},
   'lender_id': 'essai7600',
   'name': 'Essai',
   'uid': 'essai7600',
   'whereabouts': ''},
  {'country_code': 'US',
   'image': {'id': 2543845, 'template_id': 1},
   'lender_id': 'drlinda5264',
   'name': 'Dr. Linda Makuta, DDS',
   'uid': 'drlinda5264',
   'whereabouts': 'Encino CA'},
  {'image': {'id': 726677, 'template_id': 1},
   'lender_id': 'andy1386',
   'name': 'andy',
   'uid': 'andy1386',
   'whereabouts': ''},
  {'image': {'id': 726677, 'template_id': 1},
   'lender_id': 'frances9054',
   'name': 'Frances',
   'uid': 'frances9054',
 

In [74]:
def extract_loan_partners(partner_ids):
    loan_partner_details=pd.DataFrame()
    for n in partner_ids:
        d = r.get('https://api.kivaws.org/v1/partners/'+n+'.json?app_id=org.deltanalytics')
        data = json.loads(d.text)
        partners=json_normalize(data['partners'])
        loan_partner_details=loan_partner_details.append(partners, ignore_index=True)
    
    return loan_partner_details  

In [75]:
loan_partner_details=extract_loan_partners(partner_id)

386
1
156
2
133
3
218
4
388
5
164
6
138
7
202
8
258
9
262
10
526
11
520
12
466
13
477
14
397
15
512
16
505
17
500
18
502
19
436
20
491
21
469
22
276
23
322
24
473
25
405
26
340
27
350
28
341
29
412
30
286
31
447
32
277
33
324
34
282
35
213
36
385
37
259
38
257
39
212
40
203
41
336
42
345
43
272
44
142
45
24
46
36
47
92
48
27
49
25
50
6
51
32
52


In [77]:
loan_partner_details.to_csv('~/intro_to_machine_learning/data/loans_partner_details.csv')

## Pulling each loan's lender details

Now that we have selected a subset of loans to focus in on, we want to pull all of the lenders of these loans. We do so here by first creating a list of the loans we are interested in. 

In [12]:
loan_ids = df['id'].astype(int).astype(str)
loan_ids = loan_ids.unique().tolist()
loan_ids[0:5]

['1291548', '1291532', '1291530', '1291525', '1291518']

Here we define a function that will extract details of every lender who has contributed to a single loan, and then loop it over the list of loans that we created in the previous step:

In [25]:
def extract_loan_lenders(loan_ids):
    loan_lenders_details=pd.DataFrame()
    for n in loan_ids:
        d = r.get('https://api.kivaws.org/v1/loans/'+n+'/lenders.json?app_id=org.deltanalytics')
        data = json.loads(d.text)
        if len(data['lenders']) != 0:
            lenders=json_normalize(data['lenders'])
        else: lenders = pd.DataFrame()
        lenders['loan_id'] = n
        loan_lenders_details = loan_lenders_details.append(lenders, ignore_index=True)

    return loan_lenders_details  

In [ ]:
loan_lenders_details = extract_loan_lenders(loan_ids)

1291548
11
1291532
30
1291530
33
1291525
35
1291518
37
1291513
41
1291516
47
1291490
63
1291494
65
1291486
67
1291483
75
1291478
87
1291468
97
1291463
105
1291423
120
1291444
137
1291449
143
1291450
145
1291421
145
1291399
146
1291416
150
1291404
154
1291407
158
1291389
158
1291241
188
1291387
196
1291369
202
1291215
212
1291218
231
1291355
242
1291347
252
1291328
255
1291304
263
1291301
284
1291284
298
1291274
314
1291096
317
1291206
335
1291104
348
1291095
356
1291166
368
1291144
397
1291145
402
1291129
407
1291120
417
1291121
424
1291114
426
1291075
428
1291078
431
1291092
443
1291044
445
1291071
448
1291025
458
1291062
461
1291068
463
1291048
466
1291052
468
1288706
518
1291023
530
1291022
535
1290690
537
1290689
543
1290693
547
1290519
553
1290518
555
1290523
557
1290685
568
1290514
574
1290534
576
1290682
579
1290683
587
1290655
593
1290680
616
1290494
619
1290661
623
1290665
627
1290670
628
1290672
636
1290674
643
1290676
657
1290662
660
1290664
660
1290671
661
1290650
686
12906

We then write the output to a data frame. Let's take a look at what we've got! 

In [27]:
loan_lenders_details.head(100)

country_code  image.id  image.template_id                 lender_id  \
0            US    977510                  1                   tom7592   
1            AU    623712                  1            ashley74191869   
2           NaN   1158966                  1               heather3547   
3            SE   1102204                  1                 magnusang   
4            NO    659790                  1                 helge1340   
5           NaN    726677                  1         100ofhumanity1199   
6           NaN   1525019                  1                 tasia6880   
7            DE    432469                  1                  dirk1968   
8            US   1343772                  1                  beth3603   
9            US    726677                  1                  will8174   
10           CA   1492782                  1                 sandy3287   
11           CA   1186215                  1                 chris5026   
12           SE    726677                  1  energiminnesfondense7805   
13          NaN   1441656                  1                 david6847   
14           PR    726677                  1               joaquin9318   
15           DE    726677                  1                  sven7705   
16           DE   1317575                  1                ansgar5515   
17          NaN    726677                  1            annejorunn6309   
18           US   1125053                  1                bahram3005   
19          NaN    726677                  1           anthony14924365   
20           GB     35145                  1                  mark5702   
21           US      6223                  1           christopher9365   
22           IE    429766                  1                   pat7416   
23          NaN    726677                  1                       NaN   
24           US    173147                  1                 arlen2459   
25           US    726677                  1                   jay8342   
26           US    726677                  1                stuart7599   
27          NaN   1314520                  1                  rick8147   
28           US     44085                  1             laandalli5862   
29           SE    848761                  1             david12675440   
..          ...       ...                ...                       ...   
70          NaN   2430443                  1  globalpatentsolution8479   
71          NaN    726677                  1                   ben5516   
72          NaN    726677                  1              john44967045   
73           US    726677                  1                  will8174   
74           GB   1061340                  1                 clive2229   
75          NaN   1271258                  1                  john8362   
76           DE    726677                  1                  pion5294   
77           US   2037876                  1                sanjiv6738   
78           US     65589                  1                 linda3929   
79          NaN    726677                  1         100ofhumanity1199   
80           CA    726677                  1                  gwen1445   
81          NaN    726677                  1                 jesse9354   
82           US    726677                  1               christy1924   
83          NaN    726677                  1                       NaN   
84          NaN    726677                  1         karencristina6173   
85           US    726677                  1                  will8174   
86           US   1546329                  1                steven1761   
87           DE    726677                  1                marina5891   
88           US    118433                  1                   ann2750   
89           US    726677                  1         fridaymorning6726   
90           US   2525982                  1                  kitcorry   
91          NaN   2463632                  1           michael99101385   
92     

In [ ]:
loan_lenders_details.to_csv('~/intro_to_machine_learning/data/loans_lenders_details.csv')